This notebook is ran on code where instead of random movements, it goes into the opposite direction.

In [1]:
from human_aware_rl.utils import set_style
from human_aware_rl.experiments.bc_experiments import *
from human_aware_rl.experiments.pbt_experiments import *
from human_aware_rl.experiments.ppo_bc_experiments import *
from human_aware_rl.experiments.ppo_sp_experiments import *
from human_aware_rl.experiments.planning_experiments import P_BC_evaluation

best_bc_model_paths = load_pickle("data/bc_runs/best_bc_model_paths")
best_bc_models_performance = load_pickle("data/bc_runs/best_bc_models_performance")
set_style()

layouts = ['simple', 'unident_s']
delivery_horizon_dict = {"simple": 2, "unident_s": 3}

from overcooked_ai_py.mdp.overcooked_env import OvercookedEnv
from overcooked_ai_py.agents.benchmarking import AgentEvaluator
from overcooked_ai_py.agents.agent import EmbeddedPlanningAgent, AgentPair

from human_aware_rl.imitation.behavioural_cloning import get_bc_agent_from_saved

import json, copy
import numpy as np

from overcooked_ai_py.utils import save_pickle, load_pickle, cumulative_rewards_from_rew_list, save_as_json, load_from_json
from overcooked_ai_py.planning.planners import NO_COUNTERS_PARAMS, MediumLevelPlanner
from overcooked_ai_py.mdp.layout_generator import LayoutGenerator
from overcooked_ai_py.agents.agent import AgentPair, CoupledPlanningAgent, RandomAgent, GreedyHumanModel, CoupledPlanningExperimentalAgent
from overcooked_ai_py.mdp.overcooked_mdp import OvercookedGridworld, Action, OvercookedState
from overcooked_ai_py.mdp.overcooked_env import OvercookedEnv



/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/nils/minicond

In [2]:
best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

# set_global_seed(166)

# CP+HPROXY horizon 100
cp_performance = {}
# for layout in layouts:
for layout in ['simple']:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Use keras.layers.flatten instead.
Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Deprecated in favor of operator or tf.math.divide.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	3.22 seconds,   	7797 state expanded (0.33 unique) 	 ~2423.80 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	3.10 seconds,   	7826 state expanded (0.32 unique) 	 ~2525.57 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.97 seconds,   	7776 state expanded (0.33 unique) 	 ~2622.15 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.80 seconds,   	7591 state expanded (0.32 unique) 	 ~2715.48 expansions/s
First m

/home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/mdp/overcooked_env.py:162: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return np.array(trajectory), self.t, self.cumulative_sparse_rewards, self.cumulative_shaped_rewards
 20%|█████████████████                                                                    | 1/5 [00:45<03:02, 45.72s/it]

Found goal after: 	1.36 seconds,   	5161 state expanded (0.33 unique) 	 ~3802.99 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 22
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø3X X 
O ←o  →oO 
X       X 
X D X S X 


Path for last node expanded:  [None, (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 

...

 80%|████████████████████████████████████████████████████████████████████                 | 4/5 [04:53<01:23, 83.54s/it]

Found goal after: 	1.71 seconds,   	7076 state expanded (0.33 unique) 	 ~4135.26 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  206
Timestep: 100
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X ø-X X 
O   ↑1←oO 
X       X 
X D X S X 


X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	2.11 seconds,   	7797 state expanded (0.33 unique) 	 ~3701.77 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  206
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.91 seconds,   	7826 state expanded (0.32 unique) 	 ~4101.21 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  206
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.92 seconds,   	7776 state expanded (0.33 unique) 	 ~4046.26 expansions/s
First

100%|█████████████████████████████████████████████████████████████████████████████████████| 5/5 [05:31<00:00, 66.32s/it]

Found goal after: 	1.17 seconds,   	5161 state expanded (0.33 unique) 	 ~4403.78 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  206
Timestep: 22
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø3X X 
O ←o  →oO 
X       X 
X D X S X 


Path for last node expanded:  [None, (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1

{'simple': 0.0}

In [3]:
best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

# set_global_seed(166)

# CP+HPROXY horizon 100
cp_performance = {}
# for layout in layouts:
for layout in ['simple']:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.90 seconds,   	7797 state expanded (0.33 unique) 	 ~4111.62 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.83 seconds,   	7826 state expanded (0.32 unique) 	 ~4280.70 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.88 seconds,   	7776 state expanded (0.33 unique) 	 ~4140.41 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.88 seconds,   	7591 state expanded (0.32 unique) 	 ~4028.71 expansions/s
First m

Found goal after: 	0.91 seconds,   	3490 state expanded (0.33 unique) 	 ~3827.62 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 41
Joint action taken: ('interact', '←') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ←1    X 
X D XoS X 


Found goal after: 	0.97 seconds,   	3482 state expanded (0.33 unique) 	 ~3581.60 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 42
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓1    X 
X D XoS X 


Found goal after: 	0.97 seconds,   	3478 state expanded (0.33 unique) 	 ~3583.96 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 43
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓d    X 
X D XoS X 


Found goal after: 	0.89 seconds,   	3461 state expanded (0.33 unique) 	 ~3870.49 expansions/s
First motion goal:  (((3, 1), (1, 0

Found goal after: 	1.50 seconds,   	5664 state expanded (0.33 unique) 	 ~3773.70 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 70
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X ø4X X 
O ↑1    O 
X ←0    X 
X D XoS X 


Found goal after: 	1.47 seconds,   	5378 state expanded (0.33 unique) 	 ~3667.87 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 71
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø5X X 
O ↑1    O 
X ↑0    X 
X D XoS X 


Found goal after: 	1.35 seconds,   	5317 state expanded (0.33 unique) 	 ~3943.99 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 72
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O ↑1    O 
X ↓0    X 
X D XoS X 


Found goal after: 	1.36 seconds,   	4888 state expanded (0.33 unique) 	 ~3601.75 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0))

...

Found goal after: 	1.10 seconds,   	5664 state expanded (0.33 unique) 	 ~5136.02 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  90
Timestep: 70
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X ø4X X 
O ↑1    O 
X ←0    X 
X D XoS X 


Found goal after: 	1.07 seconds,   	5378 state expanded (0.33 unique) 	 ~5033.82 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  90
Timestep: 71
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø5X X 
O ↑1    O 
X ↑0    X 
X D XoS X 


Found goal after: 	1.14 seconds,   	5317 state expanded (0.33 unique) 	 ~4660.06 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  90
Timestep: 72
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O ↑1    O 
X ↓0    X 
X D XoS X 


Found goal after: 	0.97 seconds,   	4888 state expanded (0.33 unique) 	 ~5033.78 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0))

Found goal after: 	1.34 seconds,   	7034 state expanded (0.33 unique) 	 ~5262.94 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  90
Timestep: 99
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø=X X 
O ←1    O 
X   ↓0  X 
X D XoS X 




100%|████████████████████████████████████████████████████████████████████████████████████| 5/5 [08:54<00:00, 106.97s/it]

Found goal after: 	1.39 seconds,   	6551 state expanded (0.33 unique) 	 ~4725.73 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  90
Timestep: 100
Joint action taken: ('←', 'interact') 	 Reward: 0 + shape * 0 
X X ø=X X 
O ←o    O 
X ←0    X 
X D XoS X 


Avg reward 40.00 (std: 0.00, se: 0.00) over 5 games of avg length 100.0


{'simple': 40.0}

horizon 100 : 40,40 
horizon 400 : 180,280

Comparison on simple (global seed 166); 
horizon 100
normal: 0 (5x) - failures 390
adjusted: 40 (5x) - failures 90

Comparison on simple (no seed);
horizon 100
normal: Avg reward 16.00 (std: 19.60, se: 8.76) (5x) - failures 284
adjusted: 40 (5x) - failures 90

In [4]:
best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

# set_global_seed(166)

# CP+HPROXY horizon 100
cp_performance = {}
# for layout in layouts:
for layout in ['simple']:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.81 seconds,   	7797 state expanded (0.33 unique) 	 ~4318.30 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.61 seconds,   	7826 state expanded (0.32 unique) 	 ~4869.42 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.69 seconds,   	7776 state expanded (0.33 unique) 	 ~4613.66 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.73 seconds,   	7591 state expanded (0.32 unique) 	 ~4396.60 expansions/s
First m

Timestep: 82
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ↑o  O 
X   ↓o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((2, 1), (0, -1)))]
State of last node expanded:  Players: ((2, 2) facing (0, 1) holding onion@(2, 2), (2, 1) facing (0, -1) holding onion@(2, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((2, 1), (0, -1)), ((2, 1), (0, -1))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f9f6d7b8cd0>, 1)]
COUPLED PLANNING FAILURE
failures:  61
Timestep: 83
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ↑o  O 
X   ↓o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((2, 1), (0, -1)))]
State of last node expanded:  Players: ((2, 2) facing (0, 1) holding onion@(2, 2), (2, 1) facing (0, -1) holding onion@(2, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 

Timestep: 162
Joint action taken: ('↓', 'interact') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ↑o  O 
X   ↓o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((2, 1), (0, -1)))]
State of last node expanded:  Players: ((2, 2) facing (0, 1) holding onion@(2, 2), (2, 1) facing (0, -1) holding onion@(2, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((2, 1), (0, -1)), ((2, 1), (0, -1))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f9f6d7882d0>, 1)]
COUPLED PLANNING FAILURE
failures:  141
Timestep: 163
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ←o    X 
X D X S X 


Path for last node expanded:  [None, (((1, 2), (0, 1)), ((3, 1), (1, 0))), (((1, 2), (0, 1)), ((3, 1), (1, 0)))]
State of last node expanded:  Players: ((1, 2) facing (0, 1) holding onion@(1, 2), (3, 1) facing (1, 0) holding onion@(3, 1)), Objects: [soup@(2, 0) with state 

...

Timestep: 248
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     ←oO 
X   ↓o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((3, 1), (1, 0))), (((2, 1), (0, -1)), ((3, 1), (1, 0)))]
State of last node expanded:  Players: ((2, 1) facing (0, -1) holding onion@(2, 1), (3, 1) facing (1, 0) holding onion@(3, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((2, 1), (0, -1)), ((3, 1), (1, 0))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f9f6c4d6410>, 1)]
COUPLED PLANNING FAILURE
failures:  1726
Timestep: 249
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     ←oO 
X   ↓o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((3, 1), (1, 0))), (((2, 1), (0, -1)), ((3, 1), (1, 0)))]
State of last node expanded:  Players: ((2, 1) facing (0, -1) holding onion@(2, 1), (3, 1) facing (1, 0) holding onion@(3

Timestep: 310
Joint action taken: ('→', '←') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ←o  O 
X   →o  X 
X D X S X 


Path for last node expanded:  [None, (((2, 1), (0, -1)), ((1, 1), (-1, 0))), (((2, 1), (0, -1)), ((1, 1), (-1, 0)))]
State of last node expanded:  Players: ((2, 1) facing (0, -1) holding onion@(2, 1), (1, 1) facing (-1, 0) holding onion@(1, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((2, 1), (0, -1)), ((1, 1), (-1, 0))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f9f6c1cd510>, 1)]
COUPLED PLANNING FAILURE
failures:  1788
Timestep: 311
Joint action taken: ('→', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   ←o  O 
X     →oX 
X D X S X 


Path for last node expanded:  [None, (((3, 1), (1, 0)), ((1, 1), (-1, 0))), (((3, 1), (1, 0)), ((1, 1), (-1, 0)))]
State of last node expanded:  Players: ((3, 1) facing (1, 0) holding onion@(3, 1), (1, 1) facing (-1, 0) holding onion@(

100%|█████████████████████████████████████████████████████████████████████████████████████| 5/5 [04:22<00:00, 52.48s/it]

Timestep: 371
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X ø20X X 
O ←o  →oO 
X       X 
X D X S X 


Path for last node expanded:  [None, (((1, 1), (-1, 0)), ((3, 1), (1, 0)))]
State of last node expanded:  Players: ((1, 1) facing (-1, 0) holding onion@(1, 1), (3, 1) facing (1, 0) holding onion@(3, 1)), Objects: [soup@(2, 0) with state ('onion', 3, 20)], Order list: ['any', 'any']
Successors for last node expanded:  [((((1, 1), (-1, 0)), ((3, 1), (1, 0))), <overcooked_ai_py.mdp.overcooked_mdp.OvercookedState object at 0x7f9f6c1c7e10>, 1)]
COUPLED PLANNING FAILURE
failures:  1849
Timestep: 372
Joint action taken: ('→', 'stay') 	 Reward: 0 + shape * 0 
X X ø20X X 
O   →o→oO 
X       X 
X D X S X 


Path for last node expanded:  [None, (((1, 1), (-1, 0)), ((3, 1), (1, 0))), (((1, 1), (-1, 0)), ((3, 1), (1, 0)))]
State of last node expanded:  Players: ((1, 1) facing (-1, 0) holding onion@(1, 1), (3, 1) facing (1, 0) holding onion@(3, 1)), Objects: [soup@(2, 0) with state ('

{'simple': 0.0}

In [5]:
best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

# set_global_seed(166)

# CP+HPROXY horizon 100
cp_performance = {}
# for layout in layouts:
for layout in ['simple']:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	3.11 seconds,   	7797 state expanded (0.33 unique) 	 ~2510.73 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.81 seconds,   	7826 state expanded (0.32 unique) 	 ~2787.01 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.91 seconds,   	7776 state expanded (0.33 unique) 	 ~2669.39 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.83 seconds,   	7591 state expanded (0.32 unique) 	 ~2680.32 expansions/s
First m

Found goal after: 	1.11 seconds,   	3490 state expanded (0.33 unique) 	 ~3155.32 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 41
Joint action taken: ('interact', '←') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ←1    X 
X D XoS X 


Found goal after: 	1.21 seconds,   	3482 state expanded (0.33 unique) 	 ~2870.88 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 42
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓1    X 
X D XoS X 


Found goal after: 	1.21 seconds,   	3478 state expanded (0.33 unique) 	 ~2867.08 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 43
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓d    X 
X D XoS X 


Found goal after: 	1.13 seconds,   	3461 state expanded (0.33 unique) 	 ~3050.83 expansions/s
First motion goal:  (((3, 1), (1, 0

Found goal after: 	1.56 seconds,   	5664 state expanded (0.33 unique) 	 ~3639.79 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 70
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X ø4X X 
O ↑1    O 
X ←0    X 
X D XoS X 


Found goal after: 	1.46 seconds,   	5378 state expanded (0.33 unique) 	 ~3671.60 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 71
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø5X X 
O ↑1    O 
X ↑0    X 
X D XoS X 


Found goal after: 	1.41 seconds,   	5317 state expanded (0.33 unique) 	 ~3763.47 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 72
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O ↑1    O 
X ↓0    X 
X D XoS X 


Found goal after: 	1.25 seconds,   	4888 state expanded (0.33 unique) 	 ~3917.62 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0))

...

Found goal after: 	1.02 seconds,   	4074 state expanded (0.33 unique) 	 ~4001.33 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((3, 1), (1, 0)))
failures:  90
Timestep: 361
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X ø17X X 
O   ↑d↑1O 
X       X 
X D XoS X 


Found goal after: 	1.14 seconds,   	4037 state expanded (0.33 unique) 	 ~3543.55 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((3, 1), (1, 0)))
failures:  90
Timestep: 362
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X ø18X X 
O   ↑d↑1O 
X       X 
X D XoS X 


Found goal after: 	0.94 seconds,   	4007 state expanded (0.33 unique) 	 ~4268.93 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((3, 1), (1, 0)))
failures:  90
Timestep: 363
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X ø19X X 
O   ↑d→1O 
X       X 
X D XoS X 


Found goal after: 	0.88 seconds,   	3930 state expanded (0.33 unique) 	 ~4483.97 expansions/s
First motion goal:  (((2, 1), 

Found goal after: 	1.13 seconds,   	4903 state expanded (0.33 unique) 	 ~4336.12 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  90
Timestep: 390
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O     →1O 
X ↓0    X 
X D XoS X 


Found goal after: 	1.12 seconds,   	5000 state expanded (0.33 unique) 	 ~4452.09 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  90
Timestep: 391
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø7X X 
O ↑0  →1O 
X       X 
X D XoS X 


Found goal after: 	1.03 seconds,   	4729 state expanded (0.33 unique) 	 ~4574.02 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  90
Timestep: 392
Joint action taken: ('↓', '↓') 	 Reward: 0 + shape * 0 
X X ø8X X 
O       O 
X ↓0  ↓1X 
X D XoS X 


Found goal after: 	1.08 seconds,   	4755 state expanded (0.33 unique) 	 ~4403.42 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)

100%|████████████████████████████████████████████████████████████████████████████████████| 5/5 [46:27<00:00, 557.42s/it]

Found goal after: 	0.97 seconds,   	4126 state expanded (0.33 unique) 	 ~4262.79 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 2), (0, 1)))
failures:  90
Timestep: 400
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X ø16X X 
O   ↑d↑1O 
X       X 
X D XoS X 


Avg reward 180.00 (std: 0.00, se: 0.00) over 5 games of avg length 400.0


{'simple': 180.0}

In [ ]:
Comparison on simple (no seed);
horizon 400
normal: 0 (5x) - failures 1877
adjusted: 180 (5x) - failures 90

In [7]:
best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

# set_global_seed(166)

# CP+HPROXY horizon 100
cp_performance = {}
# for layout in layouts:
for layout in ['unident_s']:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/unident_s_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/unident_s_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X X X X X X X X 
O   X S X O X   S 
X       P   ↑0  X 
X ↑1    P       X 
X X X D X D X X X 

Found goal after: 	50.90 seconds,   	195027 state expanded (0.30 unique) 	 ~3831.20 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P ←0    X 
X ↑1    P       X 
X X X D X D X X X 


Found goal after: 	49.65 seconds,   	192500 state expanded (0.31 unique) 	 ~3877.42 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P ↑0    X 
X ↑1    P       X 
X X X D X D X X X 


Found goal after: 	53.70 seconds,   	195272 state expanded (0.30 unique) 	 ~3636.16 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward

Found goal after: 	0.93 seconds,   	4717 state expanded (0.36 unique) 	 ~5092.44 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 25
Joint action taken: ('↑', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø8↑0    X 
X ↓o    ø=      X 
X X X D X D X X X 


Found goal after: 	0.93 seconds,   	4645 state expanded (0.36 unique) 	 ~4979.96 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 26
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø9↑o    X 
X ↓o    ø=      X 
X X X D X D X X X 


Found goal after: 	0.11 seconds,   	559 state expanded (0.42 unique) 	 ~5110.90 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 27
Joint action taken: ('↓', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø10      X 
X ↓o    ø=↓o    X 
X X X D X D X X X 




Found goal after: 	3.59 seconds,   	17572 state expanded (0.37 unique) 	 ~4900.56 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oP ←o    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	3.70 seconds,   	18626 state expanded (0.37 unique) 	 ~5029.43 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-←0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	3.97 seconds,   	18625 state expanded (0.37 unique) 	 ~4689.76 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-↑0    X 
X       ø20      X 
X X X D X

...

Found goal after: 	0.03 seconds,   	97 state expanded (0.87 unique) 	 ~2964.15 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (0, -1)))
failures:  0
Timestep: 352
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑sø-←0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	96 state expanded (0.86 unique) 	 ~2878.97 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (0, -1)))
failures:  0
Timestep: 353
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑sø-↑0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	68 state expanded (0.94 unique) 	 ~2823.05 expansions/s
First motion goal:  (((5, 3), (0, 1)), ((3, 2), (0, -1)))
failures:  0
Timestep: 354
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑sø-      X 
X       ø20↓0    X 
X X X D X D X

Found goal after: 	2.10 seconds,   	10631 state expanded (0.34 unique) 	 ~5055.43 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 377
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø16      X 
X       ø=↓o    X 
X X X D X D X X X 


Found goal after: 	2.06 seconds,   	10630 state expanded (0.34 unique) 	 ~5155.55 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 378
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø17      X 
X       ø=←o    X 
X X X D X D X X X 


Found goal after: 	1.80 seconds,   	9946 state expanded (0.34 unique) 	 ~5517.80 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 379
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø18      X 
X       ø1←0    X 
X X 

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [2:39:31<00:00, 1914.22s/it]

Found goal after: 	0.02 seconds,   	102 state expanded (0.55 unique) 	 ~4503.74 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 393
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø15      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	90 state expanded (0.58 unique) 	 ~4092.98 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø16      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	75 state expanded (0.64 unique) 	 ~3690.31 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 395
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø17   

{'unident_s': 280.0}

In [6]:
best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

# set_global_seed(166)

# CP+HPROXY horizon 100
cp_performance = {}
# for layout in layouts:
for layout in ['unident_s']:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/unident_s_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/unident_s_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X X X X X X X X 
O   X S X O X   S 
X       P   ↑0  X 
X ↑1    P       X 
X X X D X D X X X 

Found goal after: 	44.48 seconds,   	195027 state expanded (0.30 unique) 	 ~4384.11 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P ←0    X 
X ↑1    P       X 
X X X D X D X X X 


Found goal after: 	43.46 seconds,   	192500 state expanded (0.31 unique) 	 ~4429.21 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P ↑0    X 
X ↑1    P       X 
X X X D X D X X X 


Found goal after: 	44.05 seconds,   	195272 state expanded (0.30 unique) 	 ~4432.48 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward

Found goal after: 	0.94 seconds,   	4717 state expanded (0.36 unique) 	 ~5009.80 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 25
Joint action taken: ('↑', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø8↑0    X 
X ↓o    ø=      X 
X X X D X D X X X 


Found goal after: 	0.96 seconds,   	4645 state expanded (0.36 unique) 	 ~4816.95 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 26
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø9↑o    X 
X ↓o    ø=      X 
X X X D X D X X X 


Found goal after: 	0.12 seconds,   	559 state expanded (0.42 unique) 	 ~4639.38 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 27
Joint action taken: ('↓', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø10      X 
X ↓o    ø=↓o    X 
X X X D X D X X X 




Found goal after: 	3.64 seconds,   	17572 state expanded (0.37 unique) 	 ~4830.54 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oP ←o    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	3.44 seconds,   	18626 state expanded (0.37 unique) 	 ~5420.57 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-←0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	3.81 seconds,   	18625 state expanded (0.37 unique) 	 ~4883.86 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-↑0    X 
X       ø20      X 
X X X D X

...

Found goal after: 	0.05 seconds,   	97 state expanded (0.87 unique) 	 ~2101.91 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (0, -1)))
failures:  0
Timestep: 352
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑sø-←0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.05 seconds,   	96 state expanded (0.86 unique) 	 ~2089.07 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (0, -1)))
failures:  0
Timestep: 353
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑sø-↑0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	68 state expanded (0.94 unique) 	 ~2014.00 expansions/s
First motion goal:  (((5, 3), (0, 1)), ((3, 2), (0, -1)))
failures:  0
Timestep: 354
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑sø-      X 
X       ø20↓0    X 
X X X D X D X

Found goal after: 	2.74 seconds,   	10631 state expanded (0.34 unique) 	 ~3875.80 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 377
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø16      X 
X       ø=↓o    X 
X X X D X D X X X 


Found goal after: 	2.57 seconds,   	10630 state expanded (0.34 unique) 	 ~4137.03 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 378
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø17      X 
X       ø=←o    X 
X X X D X D X X X 


Found goal after: 	2.51 seconds,   	9946 state expanded (0.34 unique) 	 ~3966.57 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 379
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø18      X 
X       ø1←0    X 
X X 

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [2:52:20<00:00, 2068.08s/it]

Found goal after: 	0.03 seconds,   	90 state expanded (0.58 unique) 	 ~2745.42 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø16      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	75 state expanded (0.64 unique) 	 ~2723.74 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 395
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø17      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	73 state expanded (0.74 unique) 	 ~2469.80 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 396
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø18      X

{'unident_s': 280.0}